<a href="https://colab.research.google.com/github/pthinh14/triplet-loss/blob/master/triplet_loss_keras.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [9]:
#from google.colab import drive
#drive.mount('/content/drive')

In [10]:
# %pip install tensorflow==2.0.0
#!pip install tensorflow-gpu --upgrade
import tensorflow as tf
tf.compat.v1.enable_eager_execution()
import tensorflow.keras.applications.inception_v3 as kai
import tensorflow.keras.layers as kl
import tensorflow.keras.models as km
import tensorflow.keras.callbacks as KC
from tensorflow.keras import backend as K
import matplotlib.pyplot as plt

## required for semi-hard triplet loss:
from tensorflow.python.ops import array_ops
from tensorflow.python.ops import math_ops
from tensorflow.python.framework import dtypes

import os
import numpy as np
from itertools import islice
import random
from sklearn.preprocessing import LabelEncoder

num_classes_per_batch = 4
num_images_per_class = 8

base_path= '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/'
IMG_TYPES = ['.png', '.jpg']
IMG_SIZE = 128

le = LabelEncoder()


In [11]:
!pip install -q -U tensorflow>=1.7
import tensorflow
tensorflow.__version__

'2.1.0-dev20191111'

In [12]:
def load_data(path=base_path):
    directories = os.listdir(path)
    #print(directories)
    img = {}
    for directory in directories:
        cur_path = os.path.join(base_path, directory)
        #print(cur_path)
        _, _, filenames = next(os.walk(cur_path))
        for filename in filenames:
            if os.path.splitext(filename)[1] in IMG_TYPES:
                if directory not in img:
                    img[directory ] = [os.path.join(base_path + directory , filename)]
                else:
                    img[directory].append(
                        os.path.join(base_path + directory , filename))

    label_encode = le.fit_transform(list(img.keys()))
    return img, label_encode

In [13]:
img, label_encode = load_data(base_path)

In [14]:
img

{'113': ['/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_02.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_06.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_08.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_05.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_07.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_01.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_04.png',
  '/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSION_MERGE/SESSION1/113/fish_2_113_03.png'],
 '099': ['/media/xingbo/Storage/fish_identification/data/SESSION_AQUARIUM/SESSIO

In [15]:
def triplet_loss(y_true, y_pred):
    embeddings = K.cast(y_pred, 'float32')
    
    embeddings = y_pred
    anchor_positive = embeddings[:num_images_per_class]
    negative = embeddings[num_images_per_class:]

    # Compute pairwise distance between all of anchor-positive
    dot_product = K.dot(anchor_positive, K.transpose(anchor_positive))
    square = K.square(anchor_positive)
    a_p_distance = K.reshape(K.sum(square, axis=1), (-1,1)) - 2.*dot_product  + K.sum(K.transpose(square), axis=0) + 1e-6
    a_p_distance = K.maximum(a_p_distance, 0.0) ## Numerical stability

    # Compute distance between anchor and negative
    dot_product_2 = K.dot(anchor_positive, K.transpose(negative))
    negative_square = K.square(negative)
    a_n_distance = K.reshape(K.sum(square, axis=1), (-1,1)) - 2.*dot_product_2  + K.sum(K.transpose(negative_square), axis=0)  + 1e-6
    a_n_distance = K.maximum(a_n_distance, 0.0) ## Numerical stability
    
    hard_negative = K.reshape(K.min(a_n_distance, axis=1), (-1, 1))
    
    distance = (a_p_distance - hard_negative + 0.2)
    loss = K.mean(K.maximum(distance, 0.0))/(2.)
            
    return loss
    # print(y_true)
    # print(y_pred)
    # y_pred = K.l2_normalize(y_pred,axis=1)
    # batch = 2
    # ref1 = y_pred[0:1,:]
    # pos1 = y_pred[1:num_images_per_class,:]
    # neg1 = y_pred[num_images_per_class:,:]
    # print(ref1)
    # print(pos1)
    # print(neg1)
    # dis_pos = K.sum(K.square(ref1 - pos1), axis=1, keepdims=True)
    # dis_neg = K.sum(K.square(ref1 - neg1), axis=1, keepdims=True)
    # dis_pos = K.sqrt(dis_pos)
    # dis_neg = K.sqrt(dis_neg)
    # a1 = 0.6
    # d1 = K.maximum(0.0,dis_pos-dis_neg+a1)
    # return K.mean(d1)


def build_model(image_shape=(IMG_SIZE, IMG_SIZE, 3), embedding_length=128, trainable=True):
    backbone = kai.InceptionV3(input_shape=image_shape, include_top=False)
    backbone.trainable = trainable
    x = kl.GlobalMaxPooling2D()(backbone.output)
    x = kl.Dense(embedding_length * 2)(x)
    x = kl.Dense(embedding_length)(x)
    embedding = kl.Dense(embedding_length, name='embedding')(x)
    model = km.Model(inputs=[backbone.input], outputs=[embedding])
    # opt = tf.train.AdamOptimizer(0.0001)
    model.compile(loss=triplet_loss, optimizer='adam')
    # model.summary()
    return model



In [16]:
def tfdata_generator(images, labels, is_training, batch_size=128):
    '''Construct a data generator using tf.Dataset'''
    num_labels = len(images)
    def preprocess_fn(filename, label):
        '''A transformation function to preprocess raw data
        into trainable input. '''
        image_string = tf.io.read_file(filename)

        #Don't use tf.image.decode_image, or the output shape will be undefined
        image = tf.image.decode_png(image_string, channels=3)

        #This will convert to float values in [0, 1]
        image = tf.image.convert_image_dtype(image, tf.float32)

        resized_image = tf.image.resize(image, [IMG_SIZE, IMG_SIZE])
        return resized_image, label


    def generator():
        while True:
            # Sample the labels that will compose the batch
            chosen_labels = random.sample(range(num_labels),
                                        num_classes_per_batch)
            for label in chosen_labels:
                for _ in range(num_images_per_class):
                    # yield images[label][np.random.choice(range(num_images_per_class))]
                    yield label_encode[label]

    datasets = []
    for i in range(len(img)):
        filenames = img[le.inverse_transform([i])[0]]
        labels = [i for _ in range(len(filenames))]
        dataset = tf.data.Dataset.from_tensor_slices((filenames, labels))
        datasets.append(dataset)
    
    # dataset = [tf.data.Dataset.from_tensor_slices((images, label_encode))]

    choice_dataset = tf.data.Dataset.from_generator(generator, tf.int64)
    # for d in choice_dataset:
    #     print(d)
    dataset = tf.data.experimental.choose_from_datasets(datasets, choice_dataset)
    # for image_number, label in dataset.batch(4).take(20):
    #     print("images {} from classes {}".format(image_number.numpy(), label.numpy()))
    dataset = dataset.map(preprocess_fn, num_parallel_calls=tf.data.experimental.AUTOTUNE)
    dataset = dataset.batch(batch_size, drop_remainder=True if is_training else False)

    dataset = dataset.repeat()
    dataset = dataset.prefetch(1)
    return dataset

In [ ]:

# try:
#     device_name = os.environ["COLAB_TPU_ADDR"]
#     TPU_ADDRESS = "grpc://" + device_name
#     print("Found TPU at: {}".format(TPU_ADDRESS))
# except KeyError:
#     print("TPU not found")

print("hello world")

# data = DataLoader()
model = build_model(trainable=True)
STEPS_PER_EPOCH = 100
batch_size = num_classes_per_batch*num_images_per_class

img, label_encode = load_data()

inc = iter(img.items())
splitting_point = int(len(label_encode)*0.8)
x_train = dict(islice(inc, splitting_point))
x_test = dict(inc)
y_train = label_encode[:splitting_point]
y_test = label_encode[splitting_point:]
training_set = tfdata_generator(x_train, y_train, is_training=True)
validation_set = tfdata_generator(x_test, y_test, is_training=True)


inc = iter(training_set)

while True:
    try:
        image_batch, label_batch = next(inc)
        imgs = image_batch.numpy()
        labels = label_batch.numpy()
        for i in range(len(imgs)):
            print(imgs[i])
        
    except:
        break
   

hello world
[[[0.67381966 0.65439653 0.43140057]
  [0.70136154 0.70525515 0.45100567]
  [0.7388568  0.74462557 0.5414744 ]
  ...
  [0.16633415 0.25280967 0.06727493]
  [0.16714154 0.25068665 0.07439988]
  [0.1491719  0.26998812 0.12050986]]

 [[0.6087919  0.60897034 0.35807917]
  [0.6805679  0.68894637 0.4329785 ]
  [0.6640569  0.66797847 0.5032726 ]
  ...
  [0.15917586 0.22773278 0.07566056]
  [0.16072305 0.2145374  0.08272059]
  [0.09660012 0.19848886 0.07606591]]

 [[0.46799228 0.49686974 0.2712689 ]
  [0.58884805 0.60994184 0.37570468]
  [0.6814179  0.6891702  0.5257418 ]
  ...
  [0.14868973 0.2084395  0.07399651]
  [0.14050803 0.19620286 0.08454721]
  [0.10145976 0.17314646 0.08641238]]

 ...

 [[0.4908324  0.45061463 0.3497314 ]
  [0.3411361  0.3670074  0.21164031]
  [0.40944344 0.41587725 0.30025223]
  ...
  [0.29944035 0.29685473 0.15002352]
  [0.35117584 0.34390923 0.22309494]
  [0.34313092 0.355066   0.24794732]]

 [[0.4858483  0.4562221  0.34249657]
  [0.34279943 0.38340995 

[[[0.6787863  0.6762757  0.45109138]
  [0.86733645 0.8489694  0.5956083 ]
  [0.54893017 0.5226047  0.3324304 ]
  ...
  [0.28210223 0.3681542  0.15970477]
  [0.162649   0.2854689  0.10435953]
  [0.22972815 0.277143   0.10245518]]

 [[0.5933274  0.6011441  0.4087352 ]
  [0.78775734 0.7877023  0.54612833]
  [0.60955966 0.563099   0.37512895]
  ...
  [0.31391573 0.3736382  0.18106134]
  [0.17500198 0.2803969  0.08786765]
  [0.2064561  0.27436632 0.11791861]]

 [[0.5554212  0.5521889  0.37587798]
  [0.8093919  0.8274051  0.60620254]
  [0.63356066 0.58160627 0.38751283]
  ...
  [0.3304011  0.3807381  0.20584533]
  [0.26512513 0.299376   0.13224979]
  [0.18862474 0.26773658 0.11300474]]

 ...

 [[0.47429296 0.4868615  0.32330772]
  [0.47546038 0.4657121  0.34717807]
  [0.5261247  0.53159904 0.38603666]
  ...
  [0.2741575  0.29869795 0.1870413 ]
  [0.49484813 0.48828533 0.34870353]
  [0.37023753 0.3393197  0.2568152 ]]

 [[0.45473203 0.48698404 0.3004254 ]
  [0.48683307 0.47506836 0.35342038]


  [0.39063612 0.39878562 0.25587812]]]
[[[0.98471206 0.9786306  0.73844975]
  [0.7832173  0.76350224 0.5452753 ]
  [0.8251924  0.82196665 0.61606926]
  ...
  [0.47570926 0.5242605  0.30189756]
  [0.45983902 0.53002894 0.24046095]
  [0.32625178 0.35543156 0.15776439]]

 [[0.91601026 0.9129181  0.7213651 ]
  [0.63673204 0.61576086 0.3702339 ]
  [0.88335127 0.87340266 0.66337574]
  ...
  [0.4377324  0.4887128  0.3083206 ]
  [0.3006853  0.33751127 0.2215799 ]
  [0.47026163 0.53149676 0.29536456]]

 [[0.8342219  0.8199713  0.620085  ]
  [0.69782656 0.660541   0.41450858]
  [0.74573606 0.73789287 0.50845045]
  ...
  [0.41246545 0.46553114 0.2618586 ]
  [0.3694938  0.39581805 0.2130327 ]
  [0.66149324 0.70855206 0.46541482]]

 ...

 [[0.7971003  0.7578103  0.62301224]
  [0.65541345 0.6203934  0.42697614]
  [0.6942402  0.645485   0.48145512]
  ...
  [0.5303749  0.47729388 0.32361344]
  [0.4375264  0.42841607 0.29814646]
  [0.36495098 0.3806986  0.2532782 ]]

 [[0.82963717 0.7878633  0.6691898 

  [0.1807041  0.20423353 0.14933155]]]
[[[0.44142944 0.47434133 0.2734177 ]
  [0.46613055 0.42830437 0.20497224]
  [0.40513214 0.4130444  0.22257255]
  ...
  [0.32380515 0.3888096  0.19316007]
  [0.28992483 0.35170487 0.16119792]
  [0.28630367 0.40624556 0.18240823]]

 [[0.46176288 0.4629794  0.27748796]
  [0.69074386 0.59674317 0.374443  ]
  [0.40042788 0.4170792  0.21714048]
  ...
  [0.3660069  0.41780135 0.2015636 ]
  [0.28560048 0.3880283  0.17348532]
  [0.31173855 0.39427537 0.16863194]]

 [[0.5781788  0.5207646  0.34590244]
  [0.7428769  0.68254495 0.43959048]
  [0.43102923 0.43883634 0.24857718]
  ...
  [0.3408174  0.4097972  0.18717156]
  [0.32539937 0.39867443 0.19560638]
  [0.3308129  0.36661252 0.18520898]]

 ...

 [[0.3267613  0.35029072 0.20770493]
  [0.5025714  0.5121149  0.3578727 ]
  [0.5416685  0.53577936 0.34453982]
  ...
  [0.3314406  0.3697525  0.21771511]
  [0.288464   0.25369072 0.16510311]
  [0.2944162  0.27460885 0.1622239 ]]

 [[0.4004596  0.3955946  0.2967543 

[[[0.4746471  0.46807542 0.31760052]
  [0.45727143 0.47906983 0.27925363]
  [0.47140932 0.50077814 0.28406864]
  ...
  [0.3804082  0.41232592 0.31245142]
  [0.23875973 0.3055183  0.11518436]
  [0.6600172  0.679717   0.4616563 ]]

 [[0.48740453 0.5247973  0.31176114]
  [0.5902417  0.588143   0.35549897]
  [0.44237453 0.46911132 0.2600892 ]
  ...
  [0.267898   0.29631084 0.21787949]
  [0.28940946 0.34823298 0.1868972 ]
  [0.40631807 0.42774883 0.29276106]]

 [[0.46609038 0.5026559  0.27739552]
  [0.57690907 0.59167624 0.34288636]
  [0.437945   0.46397117 0.23414595]
  ...
  [0.18040821 0.22231998 0.12235042]
  [0.31627735 0.37464136 0.23392443]
  [0.27735925 0.30791992 0.2172643 ]]

 ...

 [[0.4816881  0.47211397 0.31132963]
  [0.46155027 0.4071079  0.2755055 ]
  [0.41302156 0.4227792  0.29260167]
  ...
  [0.30003047 0.31179518 0.20153171]
  [0.27120996 0.31042564 0.17701572]
  [0.32090077 0.30428007 0.17102332]]

 [[0.4795055  0.48762438 0.32081982]
  [0.4628627  0.44562927 0.31439456]


...

[[[0.11333343 0.18372098 0.08940262]
  [0.18023431 0.2098146  0.1235141 ]
  [0.16539498 0.18347096 0.1201975 ]
  ...
  [0.06825155 0.15919448 0.10445324]
  [0.06646418 0.19961238 0.07617553]
  [0.09694472 0.20788223 0.05904643]]

 [[0.08803083 0.17638467 0.08798087]
  [0.16504289 0.1900276  0.10980393]
  [0.13628983 0.19791669 0.11096815]
  ...
  [0.06148496 0.12781462 0.08288509]
  [0.15392618 0.27840537 0.15504444]
  [0.09805987 0.1960991  0.07663909]]

 [[0.10414357 0.14649604 0.091908  ]
  [0.18401538 0.20081992 0.12799516]
  [0.1397707  0.22038558 0.12126932]
  ...
  [0.08281957 0.10854074 0.05019562]
  [0.1969363  0.26866612 0.12956166]
  [0.0771795  0.17129715 0.07531063]]

 ...

 [[0.35938632 0.34873986 0.25947824]
  [0.26766238 0.29897365 0.19185236]
  [0.35701716 0.31231266 0.26132995]
  ...
  [0.1786529  0.19748776 0.14352022]
  [0.2138094  0.25988856 0.19867933]
  [0.17748563 0.19161695 0.12828621]]

 [[0.3481165  0.35954416 0.26363426]
  [0.25775057 0.28520155 0.21819788]


[[[0.4921267  0.48074496 0.32898328]
  [0.54316735 0.5388628  0.35770476]
  [0.5039384  0.44511488 0.29217368]
  ...
  [0.2866539  0.37228444 0.21442688]
  [0.14123757 0.17417262 0.05260399]
  [0.1543505  0.24177392 0.12884499]]

 [[0.42282495 0.3784469  0.22942728]
  [0.44397765 0.4372834  0.28673193]
  [0.51795524 0.4570169  0.31042027]
  ...
  [0.21480235 0.2723851  0.1300597 ]
  [0.15306373 0.1734375  0.05540748]
  [0.14886643 0.18684131 0.10257354]]

 [[0.4572151  0.38465077 0.23167893]
  [0.45419374 0.41680098 0.26580524]
  [0.52864736 0.4674924  0.32552084]
  ...
  [0.17897837 0.20439197 0.09072775]
  [0.1614286  0.1928318  0.07126316]
  [0.13487932 0.1976857  0.09767038]]

 ...

 [[0.5420193  0.54986244 0.39497584]
  [0.5315447  0.5267779  0.35814774]
  [0.54866433 0.5361337  0.38394612]
  ...
  [0.44192562 0.4301609  0.30074912]
  [0.42772675 0.40419734 0.26302084]
  [0.44598687 0.41069275 0.2930763 ]]

 [[0.58840364 0.55764383 0.39109957]
  [0.5381434  0.5398285  0.34666002]


[[[0.51973206 0.51801175 0.3286888 ]
  [0.5685113  0.5889003  0.37528208]
  [0.62374246 0.5983902  0.44551796]
  ...
  [0.20922206 0.34030366 0.10019927]
  [0.28207573 0.3487424  0.14482081]
  [0.21300703 0.33390623 0.11238506]]

 [[0.51644105 0.47524178 0.30619135]
  [0.53079045 0.55697    0.3633272 ]
  [0.64174366 0.6093444  0.48572236]
  ...
  [0.20871739 0.31887326 0.12583649]
  [0.2787729  0.35059294 0.15041362]
  [0.20340225 0.31623927 0.11628222]]

 [[0.4922405  0.455576   0.28511006]
  [0.5407861  0.55443496 0.37634024]
  [0.59393567 0.5937562  0.45914027]
  ...
  [0.21917337 0.32870772 0.13747057]
  [0.26855907 0.34565592 0.13389121]
  [0.19597122 0.30577514 0.11443015]]

 ...

 [[0.56434584 0.5428463  0.3739967 ]
  [0.53706294 0.5449061  0.35922858]
  [0.5378199  0.53772247 0.3418909 ]
  ...
  [0.32941177 0.3114277  0.18350184]
  [0.3006213  0.31413803 0.16971365]
  [0.35948974 0.3804075  0.24898127]]

 [[0.5647059  0.5572166  0.37929672]
  [0.5571108  0.53487605 0.37235546]


[[[0.5680977  0.5575682  0.3706761 ]
  [0.55725855 0.5887738  0.39884377]
  [0.54089046 0.56685555 0.40161353]
  ...
  [0.33805567 0.40044373 0.1991472 ]
  [0.18714942 0.2131145  0.09600358]
  [0.32013032 0.38008583 0.1974418 ]]

 [[0.5466557  0.52081317 0.34471023]
  [0.5461413  0.5484077  0.34271067]
  [0.571381   0.5949104  0.42128906]
  ...
  [0.29070777 0.34560972 0.2133334 ]
  [0.19669507 0.21791138 0.12717915]
  [0.4852257  0.53978986 0.3501154 ]]

 [[0.5474716  0.5177535  0.36522588]
  [0.5386208  0.5512562  0.34281558]
  [0.5333766  0.556906   0.3765138 ]
  ...
  [0.17891464 0.24083254 0.13924496]
  [0.24832411 0.28299907 0.17257488]
  [0.45779806 0.49825454 0.35727718]]

 ...

 [[0.48599964 0.43766853 0.32957304]
  [0.50735295 0.47907478 0.36452207]
  [0.46898538 0.45808825 0.3286166 ]
  ...
  [0.3076078  0.34826344 0.22277325]
  [0.36507103 0.3689926  0.21212986]
  [0.32418087 0.35863164 0.2370711 ]]

 [[0.43751535 0.45175683 0.31603375]
  [0.5212623  0.48258275 0.34747243]


[[[0.45569295 0.43849012 0.28744844]
  [0.6101611  0.6508949  0.45633456]
  [0.38809493 0.33949268 0.2228554 ]
  ...
  [0.08038564 0.11509262 0.04712136]
  [0.05185356 0.12771674 0.08856453]
  [0.06500944 0.12332746 0.0467956 ]]

 [[0.4735401  0.44084638 0.27614048]
  [0.45867774 0.49815384 0.3190178 ]
  [0.34762755 0.31822285 0.19386926]
  ...
  [0.09193463 0.1257122  0.04513622]
  [0.05864839 0.12047437 0.06070108]
  [0.06453583 0.1185018  0.02783772]]

 [[0.47786963 0.42771897 0.2857316 ]
  [0.3893359  0.4063014  0.23139638]
  [0.26977283 0.2698125  0.12493598]
  ...
  [0.11039783 0.14682552 0.04998469]
  [0.0818743  0.13901278 0.07134663]
  [0.0662365  0.11210298 0.02596908]]

 ...

 [[0.35783035 0.3774382  0.22367382]
  [0.4006321  0.42019    0.2806679 ]
  [0.38445437 0.41658384 0.23378387]
  ...
  [0.27064598 0.25575984 0.15045328]
  [0.3413412  0.2902074  0.19650713]
  [0.25621936 0.23963834 0.1457595 ]]

 [[0.36499852 0.38036    0.22512789]
  [0.39368942 0.43042284 0.30341607]


In [ ]:

checkpt = KC.ModelCheckpoint('./weights.{epoch:02d}-{loss:.2f}.hdf5',
                             monitor='loss',
                             verbose=0,
                             save_best_only=False, 
                             mode='auto',
                             period=1)
history = model.fit(training_set,
                    steps_per_epoch=STEPS_PER_EPOCH,
                    epochs=1,
                    validation_data=validation_set,
                    validation_steps=80,
                    #callbacks=[checkpt],
                    #class_weight=None,
                    #max_queue_size=10,
                    #workers=1,
                    #use_multiprocessing=True,
                    shuffle=True)

# Plot training & validation loss values
plt.plot(history.history['loss'])
plt.plot(history.history['val_loss'])
plt.title('Model loss')
plt.ylabel('Loss')
plt.xlabel('Epoch')
plt.legend(['Train', 'Test'], loc='upper left')
plt.show()


In [ ]:
dataset = [tf.data.Dataset.from_tensor_slices((images, label_encode))]

choice_dataset = tf.data.Dataset.from_generator(generator, tf.int64)
dataset = tf.data.experimental.choose_from_datasets(dataset, choice_dataset)
iterator_helper = dataset.make_iterable_iterator()
with tf.Session() as sess:
    filename_temp = iterator_helper.get_next()
    print(sess.run(filename_temp))
    filename_temp = iterator_helper.get_next()
    print(sess.run(filename_temp))
